# Euclide

Marc Lorenzi

20 décembre 2020

In [ ]:
import matplotlib.pyplot as plt
import math
import random

## 1. L'algorithme d'Euclide

### 1.1 L'algorithme

L'algorithme d'Euclide permet de calculer le plus grand diviseur commun de deux entiers relatifs $a$ et $b$. Le voici. 

In [ ]:
def pgcd(a, b):
    while b != 0:
        a, b = b, a % b
    return a

Pour pouvoir étudier le comportement  de cet algorithme, ajoutons un troisième paramètre `dbg` à notre fonction. 

- Si `dbg` vaut 0, elle se comporte comme la précédente.
- Si `dbg` vaut 1, elle renvoie le couple $(a\land b, N(a, b))$ où $N(a, b)$ est le nombre de divisions euclidiennes effectuées par la fonction.
- Si `dbg` vaut 2, elle affiche en plus la valeur de $a$ et $b$ à chaque itération.

In [ ]:
def pgcd(a, b, dbg=0):
    N = 0
    while b != 0:
        a, b = b, a % b
        N += 1
        if dbg == 2: print('%3d%10d%10d' % (N, a, b))
    if dbg >= 1: return (a, N)
    else: return a

In [ ]:
pgcd(913265478, 123456789, 2)

À titre d'illustration, dessinons les pgcd des couples $(a, b)$, $0\le a\le b\le 20$.

In [ ]:
def dessiner_carre(a, b, couleur):
    plt.fill([a, a + 1, a + 1, a, a], [b, b, b + 1, b + 1, b], color = couleur)

In [ ]:
def quadriller(N):
    for a in range(N + 1): plt.plot([a, a], [0, N + 1], 'k')
    for b in range(N + 1): plt.plot([0, N + 1], [b, b], 'k')

In [ ]:
def premiers_entre_eux(N):
    for a in range(N + 1):
        for b in range(N + 1):
            col = 1 - pgcd(a, b) / N
            dessiner_carre(a, b, (col, col, col))
    quadriller(N)
    plt.xlim(0, N)
    plt.ylim(0, N)
    plt.axis('off')

In [ ]:
plt.rcParams['figure.figsize'] = (8, 8)

In [ ]:
premiers_entre_eux(20)

Il s'agit maintenant de montrer que notre fonction `pgcd` fait bien ce que l'on attend d'elle. Lorsqu'on étudie un algorithme il y a au moins trois choses à regarder :

- La **terminaison** : notre fonction termine-t-elle pour toutes les valeurs des paramètres $a$ et $b$ ?
- La **correction** : renvoie-t-elle effectivement $a\land b$ ?
- La **complexité** : est-elle efficace ? Peut-on obtenir, en fonction de $a$ et $b$, une estimation du nombre d'opérations effectuées par la fonction `pgcd` ?

Nous allons répondre successivement à ces trois questions. Pour simplifier, nous prendrons $a,b\in\mathbb N$ (si $a$ ou $b$ est négatif, ce qui va suivre s'applique avec quelques petites modifications).

### 1.2 Une suite récurrente

Soit $\bot$ un objet qui n'est pas un entier naturel. L'objet $\bot$ symbolise la notion « d'indéterminé ». Soit $\tilde{\mathbb N}=\mathbb N\cup\{\bot\}$.

Pour tous $a, b\in\mathbb N$, on définit par récurrence sur $n$ une suite $(r_n)_{n\ge 0}$ d'éléments de $\tilde{\mathbb N}$ en posant

- $r_0=a$, $r_1=b$.
- Pour tout $n\ge 0$, 
    - Si $r_{n+1}=0$, alors $r_{n+2}=\bot$.
    - Si $r_{n+1}=\bot$, alors $r_{n+2}=\bot$.
    - Sinon, $r_{n+2}$ est le reste de la division euclidienne de $r_n$ par $r_{n+1}$.
   
Ainsi, deux situations peuvent *a priori* survenir :

1. Pour tout $n\in\mathbb N$, $r_n\ne \bot$, ou alors
2. Il existe un entier $n\in\mathbb N$ tel que $r_n=\bot$. Comme $r_0=a$ et $r_1=b$, cet entier $n$ est au moins égal à 2.

**Proposition.** On est dans la situation 2 si et seulement si il existe un entier $n_0\ge 1$ tel que $r_{n_0}=0$. Un tel entier est alors unique.

**Démonstration.** Exercice.

In [ ]:
def f_rec(a, b):
    if b != 0 and b != '\u22A5': return (b, a % b)
    elif b == 0: return (0, '\u22A5')
    else: return ('\u22A5', '\u22A5')

In [ ]:
def suite_rec(a, b, n):
    s = ''
    for k in range(n + 1):
        s = s + str(a)
        if k != n: s += ', '
        a, b = f_rec(a, b)
    return s

In [ ]:
print(suite_rec(12345, 54321, 10))

### 1.3 Terminaison

**Proposition.** Il existe $n\ge 1$ tel que $r_n=0$.

**Démonstration.** Supposons le contraire : pour tout $n\ge 1$, $r_n\ne 0, \bot$. Il en résulte les $r_n$ sont tous entiers, et pour tout $n\ge 0$, $r_{n+2}$ est le quotient de la division euclidienne de $r_n$ par $r_{n+1}$. Ainsi, 

$$\forall n\ge 0, r_{n+2}<r_{n+1}$$

La suite $(r_n)_{n\ge 1}$ est donc une suite strictement décroissante d'entiers naturels. Or, une telle suite ne peut pas exister.

On pose dorénavant

$$n_0=\min\{n\ge 1, r_n=0\}=\min\{n\ge 2, r_n=\bot\}-1$$

### 1.4 Correction

**Lemme.**  Soit $d\in\mathbb N$. Soit $k\in[|0,n_0-2|]$. On a $d\mathbin|r_k$ et $d\mathbin| r_{k+1}$ si et seulement si $d\mathbin| r_{k+1}$ et $d\mathbin| r_{k+2}$.

**Démonstration.** On a 

$$r_k=qr_{k+1}+r_{k+2}$$

où $q$ est le quotient de la division euclidienne de $r_k$ par $r_{k+1}$. La conclusion suit facilement.

**Proposition.** Soit $d\in\mathbb N$. Pour tout $k\in[|0,n_0-1|]$,

$$d\mathbin|a \text{ et } d\mathbin| b \iff d\mathbin| r_{k} \text{ et } d\mathbin| r_{k+1}$$

**Démonstration.** Récurrence évidente sur $k$ à l'aide du lemme précédent.

**Proposition.** $r_{n_0-1}=a\land b$.

**Démonstration.** Rappelons nous que $r_{n_0}=0$. Par la proposition précédente avec $k=n_0-1$, pour tout $d\in\mathbb N$,

$$d\mathbin|a \text{ et } d\mathbin| b \iff d\mathbin| r_{n_0-1} \text{ et } d\mathbin| 0\iff d\mathbin| r_{n_0-1}$$

Cette équivalence est caractéristique du pgcd de $a$ et $b$.

### 1.5 Une suite de Fibonacci modifiée

Soit $\delta\in\mathbb N$. Définissons par récurrence la suite $(F_n)_{n\ge 0}$ en posant $F_0=0$, $F_1=\delta$, et pour tout $n\ge 0$,

$$F_{n+2}=F_{n+1}+F_n$$

Nous allons voir que cette suite joue un rôle important dans l'étude de la complexité de l'algorithme d'Euclide.

La suite $(F_n)_{n\ge 0}$ est une suite récurrente linéaire d'ordre 2. Son équation caractéristique est

$$X^2-X-1=0$$

Cette équation possède deux racines réelles $\phi=\frac{1+\sqrt 5}{2}$ et $\hat\phi=\frac{1-\sqrt 5}{2}$. Il existe donc deux réels $\lambda$ et $\mu$ tels que, pour tout $n\ge 0$, 

$$F_n=\lambda \phi^n+\mu\hat\phi^n$$

Pour $n=0$ et $n=1$ on obtient les deux égalités

$$\left\{\begin{array}{lll}
\lambda+\mu &=& 0\\
\lambda\phi+\mu\hat\phi &=& \delta\\
\end{array}\right.$$

On en déduit facilement que $\lambda = -\mu=\frac{\delta}{\phi-\hat\phi}=\frac\delta{\sqrt 5}$. Ainsi,

$$F_n=\frac{\delta}{\sqrt 5}\left(\phi^n-\hat\phi^n\right)$$

Remarquons que $-1<\hat\phi<0$. Ainsi,

$$F_n\ge \frac{\delta}{\sqrt 5}\left(\phi^n-1\right)$$

In [ ]:
def fibo(delta, n):
    a, b = 0, delta
    for k in range(n):
        a, b = b, a + b
    return a

In [ ]:
print([fibo(1, k) for k in range(11)])

### 1.6 Complexité

Soient $a,b\in\mathbb N$ pas nuls tous les deux. Soit $\delta=a\land b$. L'entier $\delta$ est donc non nul.

Notons $N(a, b)$ le nombre de divisions nécessaires au calcul de $\delta$ par la fonction `pgcd`. 

L'entier $N(a,b)$ est l'entier `N` renvoyé par la fonction `pgcd`. On a précisément $N=n_0-1$, où $n_0$ est le plus petit indice $n\ge 1$ tels que $r_n=0$.

**Proposition.** On a

$$N(a, b)\le \left\lfloor\log_\phi\left(\frac{b\sqrt 5}{\delta}+1\right)\right\rfloor$$

Nous allons procéder en plusieurs étapes.

**Lemme 1.** Pour tout $k\in[|1,n_0-2|]$, $r_k\ge r_{k+1}+r_{k+2}$.

**Démonstration.** On a $r_k=qr_{k+1}+r_{k+2}$, où $q$ est le quotient de la division euclidienne de $r_k$ par $r_{k+1}$. Comme $r_k>r_{k+1}$, on a $q\ge 1$, d'où l'inégalité cherchée.

**Lemme 2.** On a pour tout $k\in[|0, n_0-1|]$, $r_{n_0-k}\ge F_{k}$. 

**Démonstration.** On procède par récurrence à deux termes sur $k$. Tout d'abord, $r_{n_0}=0=F_0$ et $r_{n_0-1}=\delta=F_1$. Soit ensuite $k\in[|0,n_0-3|]$. Supposons  $r_{n_0-k}\ge F_{k}$ et $r_{n_0-k-1}\ge F_{k+1}$. On a alors

$$r_{n_0-k-2}\ge r_{n_0-k-1}+r_{n_0-k}\ge F_{k+1}+F_k=F_{k+2}$$

**Démonstration de la proposition.** On applique le lemme précédent à $k=n_0-1$. On obtient

$$F_{n_0-1}\le r_1=b$$

Ainsi, grâce à la minoration de $F_n$ vue plue haut,

$$\frac{\delta}{\sqrt 5}\left(\phi^{n_0-1}-1\right)\le b$$

d'où

$$\phi^{n_0-1}\le \frac{b\sqrt 5}{\delta}+1$$

D'où le résultat en passant au logarithme en base $\phi$.

La fonction `majo_div` prend en paramètres deux entiers $a$ et $b$. Elle renvoie le majorant du nombre de divisions effectuées par l'algorithme d'Euclide donné par la proposition précédente. Cette fonction renvoie 0 lorsque $a=b=0$, ce qui est effectivement la bonne valeur pour $N(0,0)$.

In [ ]:
def majo_div(a, b):
    d = pgcd(a, b)
    phi = (1 + math.sqrt(5)) / 2
    if d == 0: return 0
    else:
        return math.floor(math.log(math.sqrt(5) * b / d + 1, phi))

### 1.7 Quelques tests

Le majorant de $N(a,b)$ que nous avons trouvé n'est qu'un majorant : le nombre de divisions effectuées par l'algorithme d'Euclide peut être plus petit. Faisons un petit test. La fonction `test_majo` appelle `pgcd` sur tous les couples $(a,b)\in[[1,N|]\times [|1,N|]$. Elle renvoie un quadruplet contenant :

- Le nombre minimum de divisions effectuées.
- Le nombre maximum de divisions effectuées.
- L'écart minimum entre le nombre réel de divisions et notre majorant théorique.
- L'écart maximum entre le nombre réel de divisions et notre majorant théorique.

In [ ]:
def test_majo(N):
    m = N * [None]
    min_div = 100000000
    max_div = -1
    for i in range(N): m[i] = N * [None]
    for a in range(N):
        for b in range(N):
            d, n = pgcd(a, b, 1)
            if n < min_div: min_div = n
            if n > max_div: max_div = n
            m[a][b] = majo_div(a, b) - n
    return (min_div, max_div, min(min(m)), max(max(m)))

In [ ]:
test_majo(500)

La valeur minimale est positive (nulle, en fait), ce qui nous rassure sur le fait que notre majorant est ... un majorant. 

Affichons graphiquement le nombre réel de divisions.

In [ ]:
def test_majo2(N):
    m = N * [None]
    for i in range(N): m[i] = N * [None]
    for a in range(N):
        for b in range(N):
            d, n = pgcd(a, b, 1)
            m[b][a] = n
    plt.xlabel('a', fontsize=12)
    plt.ylabel('b', fontsize=12)
    plt.imshow(m, cmap='hot', interpolation='none', origin='lower')

In [ ]:
plt.rcParams['figure.figsize'] = (8, 8)

In [ ]:
test_majo2(128)

Pourquoi voit-on apparaître des droites ? Que sont ces petits points noirs que l'on voit un peu partout ?

### 1.8 La qualité de notre majorant

Pour certaines valeurs de $a$ et $b$ notre majorant de $N(a,b)$ est mauvais. C'est le cas lorsque $N(a,b)$ est petit. Quand cela arrive-t-il ?

On a pour tous $a,b\in\mathbb N$

- $N(a,0)=0$
- Si $b\ne 0$, alors $N(a, b)=N(b, a \bmod b) + 1$

Ainsi,

- $N(a,b)=0$ si et seulement si $b=0$.
- $N(a,b)=1$ si et seulement si $a\bmod b=0$ c'est à dire $b\mathbin| a$.
- $N(a,b)=2$ si et seulement si $N(b, a\bmod b)=1$, c'est à dire $(a\bmod b)\mathbin| b$. C'est en particulier le cas si $a\ne  b$ et $a \mathbin| b$, mais pas seulement.

La fonction `test_nb_div` dessine les couples $(a,b)\in[|0,N|[^2$ tels que $N(a,b)= k$.

In [ ]:
def test_nb_div(ax, N, k):
    m = N * [None]
    for i in range(N): m[i] = N * [-1]
    for a in range(N):
        for b in range(N):
            d, n = pgcd(a, b, 1)
            if n == k: m[b][a] = 1
    ax.imshow(m, cmap='gray', interpolation='none', origin='lower')
    ax.axis('off')

Voici les couples $(a,b)$ tels que $N(a,b)=1,2,\ldots,8$. 

In [ ]:
plt.rcParams['figure.figsize'] = (16, 8)

In [ ]:
fig, ax = plt.subplots(2, 4)
for i in range(2):
    for j in range(4):
        test_nb_div(ax[i, j], 512, 4 * i + j + 1)

- Sur le premier graphique, $N(a,b)=1$. Ce sont les points tels que $b= \frac 1 k a$, où $k$ est entier. Ces points sont sur les droites d'équations $y=\frac 1 k x$.

- Sur le second graphique, $N(a,b)=2$. Ce sont les points tels que $b= k (a \bmod b)$, où $k$ est entier. Nous avons en particulier les points tels que $a<b$ et $b=ka$. Ces points sont sur les droites d'équations $y=k x$. Il y a d'autres points. Lesquels ? Ce sont pour lesquels l'algorithme d'Euclide termine en deux divisions, c'est à dire tels que

$$a=bq+r, b=rq'$$

d'où

$$b=q'(a-bq)$$

ou encore

$$b=a\frac{q'}{1+qq'}$$

Ces points sont donc encore sur des droites, de pentes $\frac{q'}{1+qq'}$.

Je vous laisse regarder ce qui se passe sur les autres graphiques 😀.

## 2. Diophante

### 2.1 Une équation diophantienne

Une *équation diophantienne* est une équation dont les inconnues sont des entiers. Nous allons nous intéresser ici à l'une des plus simples, l'équation

$$(E)\quad ax+by=c$$

où $a,b,c\in\mathbb Z$ sont fixés, et les inconnues sont $x,y\in\mathbb Z$. Nous allons également supposer que $(a,b)\ne (0,0)$ et poser $\delta=a\land b$. On a donc $\delta\ne 0$.

### 2.2 Existence de solutions - condition nécessaire

Supposons que $(x,y)$ est une solution de $(E)$. On a 

$$c=ax+by\in a\mathbb Z+b\mathbb Z=\delta\mathbb Z$$

Ainsi, $\delta$ divise $c$. En conséquence :

**Si $\delta$ ne divise pas $c$, l'équation $(E)$ n'a pas de solution.**

Nous supposerons dorénavant que $\delta\mathbin| c$. On peut alors écrire

$$\left\{\begin{array}{rll}
a&=&\delta a_1\\
b&=&\delta b_1\\
c&=&\delta c_1\\
a_1\land b_1&=&1
\end{array}\right.$$

Comme $\delta\ne 0$, l'équation $(E)$ se simplifie en

$$(E)\quad a_1x+b_1y=c_1$$

### 2.3 Bézout : la condition nécessaire est suffisante

Le théorème de Bézout affirme qu'il existe $u,v\in\mathbb Z$ tels que

$$ua_1+vb_1=1$$

Si nous posons $x_0=uc_1$ et $y_0=vc_1$, nous obtenons

$$a_1x_0+b_1y_0=c_1$$

Ainsi, $(x_0, y_0)$ est une solution de $(E)$.

### 2.4 Euclide : trouver une solution particulière

La fonction `mod3` prend en paramètres deux triplets $(u,v,r)$ et $(u',v',r')$, où $r'\ne 0$. Si $q$ est le quotient de la division euclidienne de $r$ par $r'$, la fonction renvoie le triplet $(u-qu',v-qv',r-qr')$.

In [ ]:
def mod3(s1, s2):
    u1, v1, r1 = s1
    u2, v2, r2 = s2
    q = r1 // r2
    return [u1 - q * u2, v1 - q * v2, r1 - q * r2]

La fonciton `euclide` prend en paramètres deux entiers $a$ et $b$. Elle renvoie un triplet $(u,v,r)$ tel que $r=a\land b$ et $ua+vb=r$. Enfin, nous l'espérons. Il nous faudra évidemment le prouver.

In [ ]:
def euclide(a, b):
    s1 = [1, 0, a]
    s2 = [0, 1, b]
    while s2[2] != 0:
        s1, s2 = s2, mod3(s1, s2)
    return s1

In [ ]:
euclide(1234, 5678)

Comme nous l'avons fait pour la fonction `pgcd`, voici une version de la fonction `euclide` qui affiche les résultats intermédiaires lorsque `dbg` vaut `True`.

In [ ]:
def euclide(a, b, dbg=False):
    s1 = [1, 0, a]
    s2 = [0, 1, b]
    fmt = '%10d%10d%10d'
    if dbg: print(fmt % tuple(s1))
    while s2[2] != 0:
        s1, s2 = s2, mod3(s1, s2)
        if dbg: print(fmt % tuple(s1))
    if dbg: print(fmt % tuple(s2))
    return s1

In [ ]:
euclide(142857, 256512, dbg=True)

La fonction `verif_euclide` prend en paramètres deux entiers $a$ et $b$ et un triplet $(u,v,r)$. Elle renvoie `True` si $ua+vb=r$, et $r=a\land b$.

In [ ]:
def verif_euclide(a, b, s):
    return (a * s[0] + b * s[1] == s[2]) and pgcd(a, b) == s[2]

La fonction `test_euclide` tire au hasard deux entiers entre $-N$ et $N$. Elle teste la fonction `euclide` sur ces deux entiers.

In [ ]:
def test_euclide(N):
    a = random.randint(-N, N)
    b = random.randint(-N, N)
    s = euclide(a, b)
    print(a, b)
    print(s)
    print(verif_euclide(a, b, s))

In [ ]:
test_euclide(10 ** 20)

### 2.5 La terminaison, la correction et la complexité de `euclide`

Nous reprenons ici les notations utilisées dans l'étude de l'algorithme d'Euclide : la suite $(r_n)_{n\ge 0}$, l'entier $n_0$ qui est le plus petit $n\ge 1$ tel que $r_n=0$.

**Proposition.** On a pour tout $k\in[|1,n_0-1|]$ la propriété suivante :

Avant la $k$ième itération de la boucle `while`, $s_1=[u,v,r_k]$ et $s_2=[u',v',r_{k+1}]$, où

$$ua+vb=r_k$$

et

$$u'a+v'b=r_{k+1}$$

**Démonstration.** On fait une récurrence sur $k$.

- Pour $k=1$, c'est à dire avant d'entrer dans la boucle, on a effectivement $1a+0b=a=r_0$ et $0a+1b=b=r_1$.
- Soit $k\in[|1,n_0-2|]$. Supposons la propriété vraie pour $k$. On a $s_2[2]=r_{k+1}\ne 0$ car $k+1<n_0$. Ainsi, la fonction `mod3` est appelée. Elle renvoie un triplet $[u'',v'',r'']$. Si on appelle $q$ le quotient de la division euclidienne de $r$ par $r'$, on a $r''=r-qr'=r_k-qr_{k+1}=r_{k+2}$. De plus, $u''=u-qu'$ et $v''=v-qv'$. Ainsi,

$$u''a+v''b=(u-qu')a+(v-qv')b=(ua + vb)-q(u'a+v'b)=r_k-qr_{k+1}=r_{k+2}$$

Après exécution de la ligne `s1, s2 = s2, mod3(s1, s2)`, on a bien les valeurs attendues dans $s_1$ et $s_2$.



**Proposition.** La fonction `euclide` renvoie en $n_0-1$ itérations un triplet $(u,v,r)$ tel que $ua+vb=r$ et $r=a\land b$.

**DDémonstration.** Utilisons la proposition précédente avec $k=n_0-1$. Avant la $n_0-1$-ième itération, $s_1=[u,v, r_{n_0-1}]$ où $ua+vb=r_{n_0-1}$ et $s_2=[u',v',r_{n_0}]=[u',v',0]$. À la $n_0-1$-ième itération, la condition `S2[2] != 0` est donc fausse. La fonction termine et renvoie $s_1=[u,v,r_{n_0-1}]$. Comme $r_{n_0-1}=a\land b$, la fonction `euclide` renvoie ce que l'on attend d'elle.

**Remarque.** La fonction `euclide` a donc la même complexité que la fonction `pgcd`.

### 2.6 Gauss : trouver toutes les solutions

Soit $(x_0,y_0)$ une solution de $(E)$, c'est à dire que

$$a_1x_0+b_1y_0=c_1$$

Soit $(x,y)\in\mathbb Z^2$. Alors $(x,y)$ est solution de $(E)$ si et seulement si

$$a_1x+b_1y=a_1x_0+b_1y_0$$

ou encore

$$a_1(x-x_0)=b_1(y_0-y)$$

L'un des deux entiers $a_1$ et $b_1$ est non nul. Supposons par exemple que ce soit $a_1$. $a_1$ divise $b_1(y_0-y)$ et $a_1$ est premier avec $b_1$. Par le théorème de Gauss, $a_1$ divise $y_0-y$. Il existe donc $k\in\mathbb Z$ tel que $y_0-y=ka_1$. En reportant, on obtient

$$a_1(x-x_0)=ka_1b_1$$

En simplifiant par $a_1$, il vient $x-x_0=kb_1$.

Inversement,

$$a_1(x_0+kb_1)+b_1(y_0-ka_1)=a_1x_0+b_1y_0=c_1$$

Ainsi, les solutions de $(E)$ sont les couples $(x,y)$ de la forme

$$\left\{\begin{array}{lll}
x&=&x_0+kb_1\\
y&=&y_0-ka_1
\end{array}\right.$$

où $k\in\mathbb Z$. On vérifie facilement que si $a_1=0$ et $b_1\ne 0$, on obtient la même expression pour les solutions.

### 2.7 Une analogie avec les droites du plan

Il y a une très forte analogie entre ce que nous venons de faire et ce qui se passe avec les équations de droites du plan $\mathbb R^2$.

Soit $D$ une droite du plan $\mathbb R^2$. La droite $D$ possède une **équation cartésienne** qui est de la forme

$$(D)\quad ax+by=c$$

où $a,b,c\in\mathbb R$ et le couple $(a,b)$ est différent du couple $(0,0)$. Un **vecteur directeur** de la droite $D$ est (entre autres) le vecteur $\overrightarrow u=(b, -a)$. Si $A=(x_0,y_0)\in D$, un point $M=(x,y)\in\mathbb R^2$ appartient à $D$ si et seulement si il existe $k\in\mathbb R$ tel que

$$\overrightarrow{AM}=k\overrightarrow u$$

c'est à dire

$$\left\{\begin{array}{lll}
x&=&x_0+kb\\
y&=&y_0-ka
\end{array}\right.$$

Nous avons là ce que l'on appelle des **équations paramétriques** de la droite $D$.

Il y a ainsi correspondance entre

- D'une part, l'équation diophantienne $(E)$ et l'équation cartésienne de $D$.
- D'autre part, les solutions de $(E)$ et les équations paramétriques de $D$.

Bien entendu, la **méthode** de résolution est tout à fait différente. Trouver une solution de $(E)$ utilise l'algorithme d'Euclide, mais ce n'est certainement pas ainsi que l'on trouve un point de $D$ !

**Question.** Comment trouve-t-on un point de $D$ lorsqu'on possède une équation cartésienne de cette droite ?

### 2.8 Résoudre automatiquement

Pour faire plaisir aux pousseurs de boutons, voici une « fonction » qui **affiche** l'ensemble des solutions de l'équation diophantienne $ax+by=c$. Libre à vous d'améliorer l'affichage ...

In [ ]:
def afficher_sol_diophante(a, b, c):
    d = pgcd(a, b)
    if d == 0:
        if c != 0: print('ø')
        else: print('Z x Z')
    elif c % d != 0: print('ø')
    else:
        a, b, c = a // d, b // d, c // d
        u, v, r = euclide(a, b)
        x0, y0 = u * c, v * c
        print('{(%d %+dk, %d %+dk), k \u2208 Z}' % (x0, b, y0, -a))

In [ ]:
afficher_sol_diophante(123, 456, 63)

In [ ]:
afficher_sol_diophante(123, 456, 62)

In [ ]:
afficher_sol_diophante(0, 0, 0)